# pyart_amazon_l2_dealias_3D
#### Author: djv 6/19
This script will retrieve desired level II radar data from NexRad amazon archive.
Will apply pyart dealiasing method to data.
All data  will be saved(incl dealiased velocity) to a netcdf output file.
The dealiasaed velocity will be called __velocity_dealias__
Script will create a 2panel plot of raw and dealiased velocitys at sweep=1
Last section has capability to create comparison plots for various  sweeps using 
python widgets.

Two methods of entering input data:
    1. via text widget box holding info separated by "_"
    2. or from calling python script with command line parameters *(args_dealias.py)*
_Sample textbox info_ __sta_YYYY/MM/DD_HHMM__
                   ie __kcrp_2017/08/26_0030__

In [ ]:

import pyart
import boto3     #Boto3 is the AWS SDK,
#botocore contains core configuration utilities for boto2 and boto3,
from botocore.handlers import disable_signing
import tempfile   #Tempory files in Python.. A very useful module,
from   datetime import datetime
import pytz
import numpy as np
from   matplotlib import pyplot as plt
import matplotlib.colors as col
import matplotlib.cm as cm
import cartopy
from ipywidgets import widgets, interact, interactive, fixed, interact_manual
from IPython.display import display
import numpy as np
import sys
sys.path.insert(0, '/home/djv/python/djvlibs/')   #DEFINES DJV LIB PATH
from dvpylib_shape import *

In [ ]:
###################   MAIN PROGRAM ##################################%
#%run /home/djv/python/notebooks/radar/args_dealias.py KCRP 2017/08/26 0025 velocity 1 screen
#print("Selection loc and time:",site,idate,itime)
#print(pltvar,type(pltvar))
#print(sweep,type(sweep))

## Getting Input parameters via widget

In [ ]:
p0 = widgets.Text()
print("Enter following on 1 line spearated by _")
print("    4char station ID")
print("    date YYYY/MM/DD")
print("    time HHMM")
p0

In [ ]:
inpt=p0.value.split("_")
site=inpt[0].upper()
idate=inpt[1].split("/")
itime=inpt[2]
print("Input params: ",idate,itime,site)


### User Input parameter section
Can change these to suit your needs

In [ ]:
pltvar="velocity"                 #call velocity for dealiasing
plttyp="screen"                  #png,ps,eps,jpg,screen
radmax=250                       #radial range to plot
sweep=1
lalo_dphi=(1.1*radmax)/111.11    #RANGE OF MAXRAD TO PLOT(DEG)
ofile = site+idate[0]+idate[1]+idate[2]+"_"+itime+"_"+pltvar+"sw"+str(sweep)
ofile_nc = site+idate[0]+idate[1]+idate[2]+"_"+itime+"_"+pltvar+"allsw.nc"
opaq=1.0                         #opacity of plot(0=transparent)(NOT WORKING)
hr=int(itime[0:2])
mn=int(itime[2:])
cmap0=pyart.graph.cm.LangRainbow12
cbar="True"
noise_level = 5                  #filters out noisy areas(try vals>4) None=skip
map_res='50m'


In [ ]:
def find_radfile(radar_name, desired_datetime):
    '''
    Adapted by djv
    Find the keyname in Amazon s3 archive corresponding to a given radar site 
    and datetime(ie KBOX, 2012-10-29 10:22:00)
    
    PARAMETERS:
    radar_name : str                     Four letter radar ID
    desired_datetime : datetime          The date time desired

    RETURNS:
    file_name : string     string matching the key for the L2 radar file on AWS s3
    aws_radar:             radar object connectivn data bucket
    '''
    
    bucket = "noaa-nexrad-level2"
    # Create a s3 \"client" and set it to unsigned 
    s3 = boto3.resource('s3')
    s3.meta.client.meta.events.register('choose-signer.s3.*', disable_signing)
    aws_radar = s3.Bucket(bucket)   #connect to the bucket with the radar data

    ###### Retrieves all file names for given day and site ######
    target_string = datetime.strftime(desired_datetime, '%Y/%m/%d/'+radar_name)
    list_of_keys = [this_object.key for this_object in aws_radar.objects.filter(Prefix=target_string)]

    list_of_datetimes = []
    #### Search file closest to desired time from list of keys ####  
    for obj in aws_radar.objects.filter(Prefix=target_string):
        try:
            list_of_datetimes.append(datetime.strptime(obj.key[20:35], '%Y%m%d_%H%M%S'))
        except ValueError:
            pass #usually a tar file left in the bucket
    nearest_loc = nearest(list_of_datetimes, desired_datetime)
    file_name = list_of_keys[list_of_datetimes.index(nearest_loc)]  

#create a temporary named file
    locfile = tempfile.NamedTemporaryFile()

#fetch the data from AWS S3
    aws_radar.download_file(file_name, locfile.name)

    return file_name,locfile


In [ ]:
def map_add_on(ax,map_res,lonvals,latvals):
    import matplotlib.ticker as mticker
    import cartopy.feature as cfeature
    from metpy.plots import USCOUNTIES
################# CARTOPY ADD_ONS  ######################
    ax.add_feature(USCOUNTIES.with_scale('20m'), linewidth=1,linestyle='--',edgecolor='darkgray')
    ax.add_feature(cfeature.LAND)
    ax.add_feature(cfeature.OCEAN)
    ax.add_feature(cfeature.LAKES.with_scale(map_res), alpha=0.5)
    ax.add_feature(cfeature.RIVERS.with_scale(map_res), edgecolor='tab:blue') 
    g1=ax.gridlines(draw_labels=True,
                          linewidth=2, color='gray', alpha=0.5, linestyle='--')
    g1.xlabels_top = False
    g1.ylabels_right = False
    g1.xlocator = mticker.FixedLocator(list(lonvals))
    g1.ylocator = mticker.FixedLocator(list(latvals))


In [ ]:
def nearest(items, pivot):
# Function to find the nearest array location to a value
    return min(items, key=lambda x: abs(x - pivot))

### Defining color palette

In [ ]:
cb_pth="/home11/staff/djv/python/"
cfil=cb_pth+"djv_radar_bin5.rgb"
v0=-40
v1=75
cblab = "DbZ"
cbmin=-35
cbmax=76
cbinc=5
mask_min=0
if pltvar == "velocity":
    cfil=cb_pth+"djv_vad_bin5.rgb"
    v0=-65.
    v1=65.
    cbmin=-50
    cbmax=51
    cbinc=10  
    cblab = "m/s"
    mask_min=-999

############## Creates IR colormap ###############
chan="RADAR"
dvrad,ncolor=dvColormap(cfil,chan,"")  #RGB colorfile,channel,path
dv_cmap=col.LinearSegmentedColormap('my_colormap',dvrad,N=ncolor,gamma=1.)


### Get correct remote location for file nearest desired time

In [ ]:
#datetime(2012,10,29,10,0) returns  2012-10-29 10:00:00
radar_datetime = datetime(int(idate[0]),int(idate[1]),int(idate[2]),hr,mn)

#Connect to AWS lev2 radar repository and grab the key for desires radar+time
file_name,localfile = find_radfile(site, radar_datetime)
print(file_name)

#read that file into Py-ART!
radar = pyart.io.read(localfile.name)
radar.check_field_exists(pltvar)
nsweep=radar.nsweeps
sweeps=(np.linspace(0,nsweep-1,nsweep))
print(sweeps)
print('nsweep ',nsweep)
#radar.info('compact')


## CALCULATION SECTION
Will apply desired gate filters to data and 
calculate dealiased velocity field using _pyart_ __region_based__ algorithm

In [ ]:
###############  Extract out desired level and dealias ############
print("Applying gate filter...")
# create a gate filter which specifies gates to exclude from dealiasing
gatefilter = pyart.correct.GateFilter(radar)
gatefilter.exclude_transition()

if noise_level != None:
    vel_texture = pyart.retrieve.calculate_velocity_texture(radar, 
                  vel_field='velocity', wind_size=3)
    radar.add_field('texture', vel_texture, replace_existing=True)
    gatefilter.exclude_above('texture', noise_level)

print("OK to apply REF gatefilter")
gatefilter.exclude_invalid('reflectivity')
gatefilter.exclude_outside('reflectivity', 0, 80)

corr_vel_reg = pyart.correct.dealias_region_based(radar,vel_field=pltvar, 
        keep_original=False, gatefilter = gatefilter, centered = True)
radar.add_field(pltvar+'_dealias', corr_vel_reg, replace_existing = True)

### Write output to file in NetCDF format

In [ ]:
pyart.io.write_cfradial(ofile_nc, radar, format='NETCDF4', time_reference=None, arm_time_variables=False)

## PLOTTING SECTION
Will create 2 panel maps of raw and dealiased values

In [ ]:
#Get the date at the start of collection
index_at_start =  radar.sweep_start_ray_index['data'][0]
time_at_start_of_radar = pyart.io.cfradial.netCDF4.num2date(radar.time['data'][index_at_start], radar.time['units'])

#make a nice time stamp
pacific = pytz.timezone('US/Eastern')
local_time = pacific.fromutc(time_at_start_of_radar)
fancy_date_string = local_time.strftime(' %B %d at %I:%M %p %Z')
print(fancy_date_string)

In [ ]:
######################## PLOTTING SECTION ####################
fig = plt.figure(figsize = [10,8])
plt.subplot(2, 2, 1)
#create a Cartopy Py-ART display object
display2 = pyart.graph.RadarMapDisplay(radar)
sym='ko'

########### set up plotting range based on radar centerloc
VCP=radar.metadata['vcp_pattern']
clat=radar.latitude['data'][0]
clon=radar.longitude['data'][0]
wlon=clon-lalo_dphi
elon=clon+lalo_dphi
blat=clat-lalo_dphi
ulat=clat+lalo_dphi
lab_dphi=int(abs(wlon-elon)/3.)
tmpval=np.arange(wlon,elon+lab_dphi,lab_dphi)
lonvals=np.around(tmpval,1)
latvals=np.around(np.arange(blat,ulat+lab_dphi,lab_dphi),1)
#print(wlon,elon,blat,ulat,lonvals,latvals)
projection = cartopy.crs.PlateCarree()
#Mercator( central_longitude=clon, min_latitude=clat-5, max_latitude=clat+5)

title= site+' RAW '+pltvar+' sweep='+str(sweep)+' VCP'+str(VCP)+'\n' + fancy_date_string
newsweep=sweep
ax0=plt.subplot(1, 2, 1 ,projection=projection)
display2.plot_ppi_map(pltvar, newsweep,  vmin=v0, vmax=v1, 
           projection=projection, resolution='50m',
           lat_lines=(wlon,wlon),lon_lines=(blat,blat),
           min_lon=wlon, max_lon=elon, min_lat=blat, max_lat=ulat,
           colorbar_flag=False,colorbar_label=cblab, cmap=dv_cmap,
           title=title,alpha=opaq)
map_add_on(ax0,map_res,lonvals,latvals)
# Mark the radar and lalo lines
display2.plot_point(clon, clat, label_text=site)
display2.plot_point(clon,clat,symbol=sym,label_text=site)

############### Plot RHS panel ##############
title= site+' dealiased '+pltvar+' sweep='+str(sweep)+' VCP'+str(VCP)+'\n' + fancy_date_string

ax0=plt.subplot(1, 2, 2, projection=projection)
display2.plot_ppi_map(pltvar+'_dealias', newsweep,  vmin=v0, vmax=v1, 
           projection=projection, resolution='50m',
           min_lon=wlon, max_lon=elon, min_lat=blat, max_lat=ulat,
           lat_lines=(wlon,wlon),lon_lines=(blat,blat),
           colorbar_flag=False,colorbar_label=cblab, cmap=dv_cmap,
           title=title,alpha=opaq)
map_add_on(ax0,map_res,lonvals,latvals)
# Mark the radar and lalo lines
display2.plot_point(clon, clat, label_text=site)
display2.plot_point(clon,clat,symbol=sym,label_text=site)


###########  Plot colorbar onto given locaton on page #######
# Scalarmappable creates a blank class object for colorbar
if cbar == "True" or cbar == "true":
    cb_ax = fig.add_axes([0.95, 0.25, 0.02, 0.5])
    sm = plt.cm.ScalarMappable(cmap=dv_cmap)
    sm.set_array=([])   #or sm._A = []
    sm.set_clim(cbmin,cbmax)     #Need this for colorbar labels
    cb = plt.colorbar(sm,cax=cb_ax)
    cbticlocs=[]
    cbticlabs=[]
    for it in range(cbmin,cbmax,cbinc):
        cbticlocs.append(it)
        cbticlabs.append(str(it))
    cb.set_ticks(cbticlocs,update_ticks=True)
    cb.set_ticklabels(cbticlabs,update_ticks=True)
    cb.set_label(cblab)
    cb.ax.yaxis.set_ticks_position('left')

## Save output image if desired

In [ ]:
if  plttyp is not "screen" and plttyp is not "Screen":
    ofile=ofile+"."+plttyp
    print("Saving as... "+ofile)
    fig.savefig(ofile,format=plttyp,orientation='portrait',quality=100)

## Now create 2panel comparison w/widgets controlling sweeps

In [ ]:
import matplotlib.gridspec as gridspec
######################## PLOTTING SECTION ####################

def pltrmap(sw,var,vmin,vmax,proj,wlon,elon,blat,ulat,cmap,tit,site,latvals,lonvals,
            cbmin,cbmax,cbinc):
    sym='ko'
    gs = gridspec.GridSpec(1, 1)
    gs.update(left=0.0, right=0.45, wspace=0.005)
    ax0 = plt.subplot(gs[0],projection=proj)#121)  
    ax0.clear()
    display2.plot_ppi_map(var, int(sw),  vmin=vmin, vmax=vmax, 
           projection=proj, resolution='50m',
           lat_lines=(wlon,wlon),lon_lines=(blat,blat),ax=ax0,
           min_lon=wlon, max_lon=elon, min_lat=blat, max_lat=ulat,
           colorbar_flag=False, cmap=cmap,title=site+' Raw '+tit+' swp='+sw)
    map_add_on(ax0,map_res,lonvals,latvals)
    display2.plot_point(clon, clat, symbol=sym,label_text=site)

    gs1 = gridspec.GridSpec(1, 1)
    gs1.update(left=0.53 ,right=0.98, wspace=0.005)
    ax1 = plt.subplot(gs1[0],projection=proj)#
    ax1.clear()
    display2.plot_ppi_map(var+"_dealias", int(sw),  vmin=vmin, vmax=vmax, 
           projection=proj, resolution='50m',
           lat_lines=(wlon,wlon),lon_lines=(blat,blat),ax=ax1,
           min_lon=wlon, max_lon=elon, min_lat=blat, max_lat=ulat,
           colorbar_flag=False, cmap=cmap,title=site+' dealiased '+tit+' swp='+sw)  
    map_add_on(ax1,'50m',lonvals,latvals)
    display2.plot_point(clon, clat, symbol=sym,label_text=site)

    gs2 = gridspec.GridSpec(1, 1)
    gs2.update(left=0.99 ,right=1., bottom=0.2,top=0.8 )   
    cb_ax = plt.subplot(gs2[0])  
    cb_ax.clear()
    sm = plt.cm.ScalarMappable(cmap=dv_cmap)
    sm.set_array=([])   #or sm._A = []
    sm.set_clim(cbmin,cbmax)     #Need this for colorbar labels
    cb = plt.colorbar(sm,cax=cb_ax)
    cbticlocs=[]
    cbticlabs=[]
    for it in range(cbmin,cbmax,cbinc):
        cbticlocs.append(it)
        cbticlabs.append(str(it))
    cb.set_ticks(cbticlocs,update_ticks=True)
    cb.set_ticklabels(cbticlabs,update_ticks=True)
    cb.set_label(cblab)

fig = plt.figure(figsize = [16,8])
title= pltvar+' VCP'+str(VCP)+'\n' + fancy_date_string
newsweep=sweep
csweep=[]
for i in sweeps: csweep.append(str(int(i)))   
header_sw = widgets.Dropdown(
    options=csweep,  #['0','1', '2', '3','4','5'],
    value='1',
    description='Sweep:',
    disabled=False,
)
#Dropdown.js_on_change('value', update_curve)
#def update(selected=None):
#    t1 = sw.value
interact( pltrmap,sw=header_sw,var=fixed(pltvar),vmin=fixed(v0),vmax=fixed(v1),
         proj=fixed(projection),wlon=fixed(wlon),elon=fixed(elon),blat=fixed(blat),ulat=fixed(ulat),
         cmap=fixed(dv_cmap),tit=fixed(title),clat=fixed(clat),clon=fixed(clon),site=fixed(site),
         latvals=fixed(latvals),lonvals=fixed(lonvals),
         cbmin=fixed(cbmin),cbmax=fixed(cbmax),cbinc=fixed(cbinc) )